In [1]:
from RootInteractive.InteractiveDrawing.bokeh.bokehDrawSA import *
from RootInteractive.Tools.aliTreePlayer import *
from bokeh.io import curdoc
import os
import sys
import pytest
from pandas import CategoricalDtype
from bokeh.io import output_notebook
output_notebook()
# import logging

Welcome to JupyROOT 6.24/06
x bokehVisJS3DGraph.ts
x HistogramCDS.ts
Import  CDSCompress.ts
Import  DownsamplerCDS.ts
Import  CDSAlias.ts
Import  CDSJoin.ts


Loading BokehJS ...

In [2]:
df = pd.DataFrame(np.random.random_sample(size=(20000, 4)), columns=list('ABCD'))
initMetadata(df)
MARKERS = ['hex', 'circle_x', 'triangle','square']
markerFactor=factor_mark('DDC', MARKERS, ["A0","A1","A2","A3","A4"] )
colorFactor=factor_cmap('DDC', 'Category10_6', ["A0","A1","A2","A3","A4"] )

mapDDC={0:"A0",1:"A1",2:"A2",3:"A3",4:"A4"}
df.eval("Bool=A>0.5", inplace=True)
df.eval("BoolB=B>0.5", inplace=True)
df["AA"]=((df.A*10).round(0)).astype(CategoricalDtype(ordered=True))
df["CC"]=((df.C*5).round(0)).astype(int)
df["DD"]=((df.D*4).round(0)).astype(int)
df["DDC"]=((df.D*4).round(0)).astype(int).map(mapDDC)
df['errY']=df.A*0.02+0.02
df.head(10)
df.meta.metaData = {'A.AxisTitle': "A (cm)", 'B.AxisTitle': "B (cm)", 'C.AxisTitle': "C (s)",
                    'D.AxisTitle': "D (cm)", 'Bool.AxisTitle': "A>half"}

In [3]:
tooltips = [("VarA", "(@A)"), ("B", "(@B)"), ("C (s)", "(@C)"), ("VarD (cm)", "(@D)"),  ("VarD (1/8cm)", "(8*@D)")]

widgetParams=[
    ['range', ['A']],
    ['range', ['B', 0, 1, 0.1, 0, 1]],
    ['range', ['C'], {'type': 'minmax'}],
    ['range', ['D'], {'type': 'sigma', 'bins': 10, 'sigma': 3}],
    ['multiSelect',["BoolB"]],
]
widgetLayoutDesc=[[0, 1, 2], [3, 4], {'sizing_mode': 'scale_width'}]

In [39]:
def testBokehClientHistogram():
    output_file("test_BokehClientHistogram.html")
    histoArray = [
        {"name": "histoA", "variables": ["A"], "nbins":20, "quantiles": [.05, .5, .95], "sum_range": [[.25, .75], [.4, .6]]},
        {"name": "histoB", "variables": ["B"], "nbins":20, "range": [0, 1]},
        {"name": "histoTransform", "variables": ["(A+B)/2"], "nbins": 20, "weights": "A*C"},
    ]
    figureArray = [
        #   ['A'], ['C-A'], {"color": "red", "size": 7, "colorZvar":"C", "filter": "A<0.5"}],
        [['A'], ['histoA', '(A*A-C*C)*100'], {"size": 2, "colorZvar": "A", "errY": "errY", "errX": "0.01"}],
        [['(A+B)/2'], ['histoTransform', '(C+A)*200', '(C-A)*200']],
        [['B'], ['histoB', '(C+B)*10', '(C-B)*10'], {"size": 7, "colorZvar": "C", "errY": "errY",
                                                    "rescaleColorMapper": True}]
    ]
    figureLayoutDesc=[
        [0, 1, 2, {'commonX': 1, 'y_visible': 1, 'x_visible':1, 'plot_height': 300}],
        {'plot_height': 100, 'sizing_mode': 'scale_width', 'y_visible' : 2}
    ]
    
    xxx=bokehDrawSA.fromArray(df, "A>0", figureArray, widgetParams, layout=figureLayoutDesc, tooltips=tooltips,
                              widgetLayout=widgetLayoutDesc, sizing_mode="scale_width", nPointRender=3000, histogramArray=histoArray)
testBokehClientHistogram()

In [40]:
def testBokehClientHistogramRowwiseTable():
    output_file("test_BokehClientHistogramRowwiseTable.html")
    histoArray = [
        {"name": "histoA", "variables": ["A"], "nbins":20, "quantiles": [.05, .5, .95], "sum_range": [[.25, .75], [.4, .6]]},
        {"name": "histoB", "variables": ["B"], "nbins":20, "range": [0, 1]},
        {"name": "histoTransform", "variables": ["(A+B)/2"], "nbins": 20, "weights": "A*C"},
    ]
    figureArray = [
        [['A'], ['histoA']],
        [['B'], ['histoB'], {"show_histogram_error": True}],
        [['(A+B)/2'], ['histoTransform'], {"yAxisTitle": "sum A*C"}],
        ["tableHisto", {"rowwise": True}]
    ]
    figureLayoutDesc=[
        [0, 1, 2, {'commonX': 1, 'y_visible': 1, 'x_visible':1, 'plot_height': 300}],
        [3],
        {'plot_height': 100, 'sizing_mode': 'scale_width', 'y_visible' : 2}
    ]
    xxx = bokehDrawSA.fromArray(df, "A>0", figureArray, widgetParams, layout=figureLayoutDesc, tooltips=tooltips,
                                widgetLayout=widgetLayoutDesc, sizing_mode="scale_width", histogramArray=histoArray)
testBokehClientHistogramRowwiseTable()

In [10]:
def testBokehClientHistogramProfileA():
    output_file("test_BokehClientHistogramProfileA.html")
    histoArray = [
        {"name": "histoAB", "variables": ["A", "(A+B)/2"], "nbins": [20, 20], "axis": [0, 1], "quantiles": [.1, .5, .9]}
    ]
    figureArray = [
        [['histoAB_1.bin_center_0'], ['histoAB_1.quantile_0', 'histoAB_1.quantile_1', 'histoAB_1.quantile_2']],
        [['histoAB_1.bin_center_0'], ['histoAB_1.quantile_1', 'histoAB_1.mean']],
        [['A'], ['histoAB'], {"yAxisTitle": "(A+B)/2"}],
        [['histoAB_1.bin_center_0'], ['histoAB_1.std']],
        ["tableHisto", {"rowwise": False}]
    ]
    figureLayoutDesc=[
        [0, 1,  {'commonX': 1, 'y_visible': 1, 'x_visible':1, 'plot_height': 200}],
        [2, 3, {'y_visible': 1, 'x_visible':1, 'plot_height': 200}],
        [4, {'plot_height': 40}],
        {'plot_height': 100, 'sizing_mode': 'scale_width', 'y_visible' : 2, "size": 5}
    ]
    xxx = bokehDrawSA.fromArray(df, "A>0", figureArray, widgetParams, layout=figureLayoutDesc, tooltips=tooltips,
                                widgetLayout=widgetLayoutDesc, sizing_mode="scale_width", histogramArray=histoArray)
testBokehClientHistogramProfileA()

In [23]:
df.head()

A         B         C         D   Bool  BoolB    AA  CC  DD DDC  \
0  0.961776  0.878105  0.225505  0.755343   True   True  10.0   1   3  A3   
1  0.077050  0.483740  0.332758  0.172893  False  False   1.0   2   1  A1   
2  0.425265  0.705257  0.257979  0.815034  False   True   4.0   1   3  A3   
3  0.111056  0.691861  0.108041  0.095702  False   True   1.0   1   0  A0   
4  0.441278  0.526826  0.616510  0.120341  False   True   4.0   3   0  A0   

       errY  
0  0.039236  
1  0.021541  
2  0.028505  
3  0.022221  
4  0.028826

In [33]:
def testBokehClientHistogramProfileB():
    output_file("test_BokehClientHistogramProfileB.html")
    histoArray = [
        {"name": "histoAB", "variables": ["A", "B"], "nbins": [20, 20], "weights": "D", "axis": [0, 1], "quantiles": [.1, .5, .9]}
    ]
    figureArray = [
        [['quantile_0', 'quantile_1', 'quantile_2'], ['bin_center_1'], {"source": "histoAB_0"}],
        [['quantile_1', 'mean'], ['bin_center_1'], {"source": "histoAB_0"}],
        [['A'], ['histoAB'], {"yAxisTitle": "(A+B)/2"}],
        [['std'], ['bin_center_1'], {"source": "histoAB_0"}],
        ["tableHisto", {"rowwise": False}]
    ]
    figureLayoutDesc=[
        [2, 1,  {'commonX': 1, 'y_visible': 1, 'x_visible':1, 'plot_height': 200}],
        [2, 3, {'y_visible': 1, 'x_visible':1, 'plot_height': 200}],
        [4, {'plot_height': 40}],
        {'plot_height': 100, 'sizing_mode': 'scale_width', 'y_visible' : 2, "size": 5}
    ]
    xxx = bokehDrawSA.fromArray(df, "A>0", figureArray, widgetParams, layout=figureLayoutDesc, tooltips=tooltips,
                                widgetLayout=widgetLayoutDesc, sizing_mode="scale_width", histogramArray=histoArray)
testBokehClientHistogramProfileB()

In [32]:
def testBokehClientHistogram3d():
    output_file("test_BokehClientHistogram.html")
    histoArray = [
        {"name": "histoABC", "variables": ["(A+C)/2", "B", "C"], "nbins": [8, 10, 12], "weights": "D", "axis": [0], "sum_range": [[.25, .75]]},
    ]
    figureArray = [
        [['bin_center_1'], ['mean']],
        [['bin_center_1'], ['sum_0']],
        [['bin_center_1'], ['std']],
        {"source": "histoABC_0", "colorZvar": "bin_center_2", "size": 7}
    ]
    figureLayoutDesc=[
        [0, 1, 2, {'commonX': 1, 'y_visible': 1, 'x_visible':1, 'plot_height': 300}],
        {'plot_height': 100, 'sizing_mode': 'scale_width', 'y_visible' : 2}
    ]
    
    xxx=bokehDrawSA.fromArray(df, "A>0", figureArray, widgetParams, layout=figureLayoutDesc, tooltips=tooltips,
                              widgetLayout=widgetLayoutDesc, sizing_mode="scale_width", nPointRender=3000, histogramArray=histoArray)
testBokehClientHistogram3d()